# Week 4 - Models and Experimentation

## Step 1 Training a model

For the purposes of this demo, we will be using this [adapted demo](https://www.datacamp.com/tutorial/xgboost-in-python) and training an XGBoost model, and then doing some experimentation and hyperparameter tuning.


If running this notebook locally, use the following steps to create virtual environment:
- Don't use past python 3.10
- To create virtual environment use "venv"

`python -m venv NAME`

- Try to avoid anaconda, poetry or similar package management platforms
- To install a package use pip

`python -m pip install <package-name>`

- once you are done working with this virtual environment, deactivate it with `deactivate`

### Install packages

In [1]:
!pip install wandb -qU

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.2/2.2 MB 22.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 207.3/207.3 kB 11.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 267.1/267.1 kB 18.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 62.7/62.7 kB 4.6 MB/s eta 0:00:00


In [23]:
import xgboost as xgb
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error, mean_absolute_error, r2_score
import random
import wandb
import math
import torch, torchvision
import torch.nn as nn
import torchvision.transforms as T


### Import data

We will be using Diamonds dataset imported from Seaborn. It is also available on [Kaggle](https://www.kaggle.com/datasets/shivam2503/diamonds).

Read about the features by following the link. We will be predicting the price of diamonds.

In [3]:
diamonds = sns.load_dataset('diamonds')
diamonds.head()

carat      cut color clarity  depth  table  price     x     y     z
0   0.23    Ideal     E     SI2   61.5   55.0    326  3.95  3.98  2.43
1   0.21  Premium     E     SI1   59.8   61.0    326  3.89  3.84  2.31
2   0.23     Good     E     VS1   56.9   65.0    327  4.05  4.07  2.31
3   0.29  Premium     I     VS2   62.4   58.0    334  4.20  4.23  2.63
4   0.31     Good     J     SI2   63.3   58.0    335  4.34  4.35  2.75

In [4]:
diamonds.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 53940 entries, 0 to 53939
Data columns (total 10 columns):
 #   Column   Non-Null Count  Dtype   
---  ------   --------------  -----   
 0   carat    53940 non-null  float64 
 1   cut      53940 non-null  category
 2   color    53940 non-null  category
 3   clarity  53940 non-null  category
 4   depth    53940 non-null  float64 
 5   table    53940 non-null  float64 
 6   price    53940 non-null  int64   
 7   x        53940 non-null  float64 
 8   y        53940 non-null  float64 
 9   z        53940 non-null  float64 
dtypes: category(3), float64(6), int64(1)
memory usage: 3.0 MB


In [5]:
diamonds.shape

(53940, 10)

In [6]:
X,y = diamonds.drop('price', axis=1), diamonds[['price']]

# For the cut, color and clarity use pandas category to enable XGBoost ability to deal with categorical data.

X['cut'] = X['cut'].astype('category')
X['color'] = X['color'].astype('category')
X['clarity'] = X['clarity'].astype('category')

### Split the data and train a model

In [7]:
# Split the data
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

# Create DMatrix
dtrain = xgb.DMatrix(X_train, label=y_train, enable_categorical=True)
dtest = xgb.DMatrix(X_test, label=y_test, enable_categorical=True)

In [8]:
# Define hyperparameters
params = {"objective": "reg:squarederror", "tree_method": "hist"}

n = 100
model = xgb.train(
   params=params,
   dtrain=dtrain,
   num_boost_round=n,
)

In [9]:
# Define evaluation metrics - Root Mean Squared Error

predictions = model.predict(dtest)
rmse = mean_squared_error(y_test, predictions, squared=False)
print(f"RMSE: {rmse}")

RMSE: 545.191877397669


### Incorporate validation

In [10]:
params = {"objective": "reg:squarederror", "tree_method": "hist"}
n = 100

# Create the validation set
evals = [(dtrain, "train"), (dtest, "validation")]

In [11]:
evals = [(dtrain, "train"), (dtest, "validation")]

model = xgb.train(
   params=params,
   dtrain=dtrain,
   num_boost_round=n,
   evals=evals,
   verbose_eval=10,
)

[0]	train-rmse:2861.71326	validation-rmse:2853.85688
[10]	train-rmse:554.29819	validation-rmse:579.26422
[20]	train-rmse:493.68077	validation-rmse:547.75493
[30]	train-rmse:467.32713	validation-rmse:540.03567
[40]	train-rmse:447.40974	validation-rmse:541.70531
[50]	train-rmse:432.62075	validation-rmse:540.89769
[60]	train-rmse:422.28318	validation-rmse:540.63039
[70]	train-rmse:410.72350	validation-rmse:543.67077
[80]	train-rmse:398.24619	validation-rmse:545.08296
[90]	train-rmse:386.92486	validation-rmse:543.90036
[99]	train-rmse:379.58717	validation-rmse:545.19188


In [12]:
# Incorporate early stopping
n = 10000


model = xgb.train(
   params=params,
   dtrain=dtrain,
   num_boost_round=n,
   evals=evals,
   verbose_eval=50,
   # Activate early stopping
   early_stopping_rounds=50
)

[0]	train-rmse:2861.71326	validation-rmse:2853.85688
[50]	train-rmse:432.62075	validation-rmse:540.89769
[82]	train-rmse:394.92609	validation-rmse:544.73937


In [13]:
# Cross-validation

params = {"objective": "reg:squarederror", "tree_method": "hist"}
n = 1000

results = xgb.cv(
   params, dtrain,
   num_boost_round=n,
   nfold=5,
   early_stopping_rounds=20
)


In [14]:
results.head()

train-rmse-mean  train-rmse-std  test-rmse-mean  test-rmse-std
0      2861.512810        8.494816     2861.704341      37.144992
1      2081.847733        5.811005     2084.838207      31.889208
2      1547.031906        5.092391     1554.657450      30.699908
3      1184.129738        3.982239     1194.251600      26.940062
4       942.998782        3.327174      960.239319      24.392689

In [15]:
best_rmse = results['test-rmse-mean'].min()

best_rmse

553.4613038243663

## Start W&B


- Login into your W&B profile using the code below
- Alternatively you can set environment variables. There are several env variables which you can set to change the behavior of W&B logging. The most important are:
    - WANDB_API_KEY - find this in your "Settings" section under your profile
    - WANDB_BASE_URL - this is the url of the W&B server

- Find your API Token in "Profile" -> "Setttings" in the W&B App



In [16]:
# Log in to your W&B account
import wandb

wandb.login()

<IPython.core.display.Javascript object>

wandb: Logging into wandb.ai. (Learn how to deploy a W&B server locally: https://wandb.me/wandb-server)
wandb: You can find your API key in your browser here: https://wandb.ai/authorize
wandb: Paste an API key from your profile and hit enter, or press ctrl+c to quit:

 ··········


wandb: Appending key for api.wandb.ai to your netrc file: /root/.netrc


True

In [ ]:
# TO DO
# Start experiment tracking with W&B
# Do at least 5 experiments with various hyperparameters
# Choose any method for hyperparameter tuning: grid search, random search, bayesian search
# Describe your findings and what you see

## 👟 Run an experiment
1️⃣. **Start a new run** and pass in hyperparameters to track

2️⃣. **Log metrics** from training or evaluation

3️⃣. **Visualize results** in the dashboard

In [19]:
# Launch 5 simulated experiments
total_runs = 5
for run in range(total_runs):
    # Start a new run to track this script
    wandb.init(
        project="xgboost_run",
        name=f"experiment_{run}",
        config={
            "learning_rate": 0.01 + 0.02 * random.random(),  # Vary learning rate
            "max_depth": random.randint(3, 10),  # Vary max_depth
            "subsample": 0.5 + 0.5 * random.random(),  # Vary subsample rate
            "n_estimators": 100,
            "objective": "reg:squarederror",
            "reg_alpha": 0.001 * 10 ** random.uniform(0, 3),
            "reg_lambda": 0.01 * 10 ** random.uniform(0, 3),
            "dataset": "Boston Housing",
        }
    )

    # Create DMatrix
    dtrain = xgb.DMatrix(X_train, label=y_train, enable_categorical=True)
    dtest = xgb.DMatrix(X_test, label=y_test, enable_categorical=True)

    # Configure parameters for XGBoost
    params = {
        "objective": wandb.config.objective,
        "learning_rate": wandb.config.learning_rate,
        "max_depth": wandb.config.max_depth,
        "subsample": wandb.config.subsample,
        "tree_method": "hist",
        "reg_alpha": wandb.config.reg_alpha,
        "reg_lambda": wandb.config.reg_lambda
    }

    # Train the model
    bst = xgb.train(params, dtrain, num_boost_round=wandb.config.n_estimators, evals=[(dtest, "Test")])

    # Evaluate the model
    predictions = bst.predict(dtest)
    rmse = mean_squared_error(y_test, predictions, squared=False)
    mae = mean_absolute_error(y_test, predictions)
    r2 = r2_score(y_test, predictions)

    # Log metrics from your script to W&B
    wandb.log({
      "RMSE": rmse,
      "MAE": mae,
      "R2": r2
    })

    # Mark the run as finished
    wandb.finish()

wandb: Currently logged in as: russellspence2024 (msai490). Use `wandb login --relogin` to force relogin


[0]	Test-rmse:3878.26330
[1]	Test-rmse:3772.48418
[2]	Test-rmse:3669.99195
[3]	Test-rmse:3570.44844
[4]	Test-rmse:3473.79830
[5]	Test-rmse:3380.12458
[6]	Test-rmse:3289.39336
[7]	Test-rmse:3201.21267
[8]	Test-rmse:3115.59826
[9]	Test-rmse:3032.71012
[10]	Test-rmse:2952.05869
[11]	Test-rmse:2873.80402
[12]	Test-rmse:2798.02680
[13]	Test-rmse:2724.31190
[14]	Test-rmse:2652.32381
[15]	Test-rmse:2583.42116
[16]	Test-rmse:2516.03802
[17]	Test-rmse:2451.08844
[18]	Test-rmse:2387.87679
[19]	Test-rmse:2326.33601
[20]	Test-rmse:2267.01572
[21]	Test-rmse:2209.21898
[22]	Test-rmse:2153.27554
[23]	Test-rmse:2098.80842
[24]	Test-rmse:2046.36405
[25]	Test-rmse:1995.23859
[26]	Test-rmse:1945.86521
[27]	Test-rmse:1897.63168
[28]	Test-rmse:1850.97767
[29]	Test-rmse:1805.72554
[30]	Test-rmse:1761.47002
[31]	Test-rmse:1718.61700
[32]	Test-rmse:1677.31129
[33]	Test-rmse:1637.33803
[34]	Test-rmse:1598.79525
[35]	Test-rmse:1561.09108
[36]	Test-rmse:1524.72903
[37]	Test-rmse:1489.67920
[38]	Test-rmse:1455.48

[0]	Test-rmse:3888.05121
[1]	Test-rmse:3791.80034
[2]	Test-rmse:3698.29544
[3]	Test-rmse:3606.95292
[4]	Test-rmse:3517.70062
[5]	Test-rmse:3431.03287
[6]	Test-rmse:3346.74863
[7]	Test-rmse:3264.90973
[8]	Test-rmse:3185.79820
[9]	Test-rmse:3108.69378
[10]	Test-rmse:3033.62695
[11]	Test-rmse:2960.31557
[12]	Test-rmse:2889.01346
[13]	Test-rmse:2819.94282
[14]	Test-rmse:2752.88255
[15]	Test-rmse:2687.54174
[16]	Test-rmse:2623.79658
[17]	Test-rmse:2561.75500
[18]	Test-rmse:2501.97340
[19]	Test-rmse:2443.33456
[20]	Test-rmse:2386.44796
[21]	Test-rmse:2331.58650
[22]	Test-rmse:2278.04752
[23]	Test-rmse:2225.74191
[24]	Test-rmse:2174.75031
[25]	Test-rmse:2125.47725
[26]	Test-rmse:2077.61436
[27]	Test-rmse:2030.79249
[28]	Test-rmse:1985.83438
[29]	Test-rmse:1942.43672
[30]	Test-rmse:1899.34615
[31]	Test-rmse:1857.81522
[32]	Test-rmse:1817.88408
[33]	Test-rmse:1778.59924
[34]	Test-rmse:1740.08617
[35]	Test-rmse:1702.66603
[36]	Test-rmse:1667.53725
[37]	Test-rmse:1632.63241
[38]	Test-rmse:1598.21

[0]	Test-rmse:3885.46676
[1]	Test-rmse:3786.86520
[2]	Test-rmse:3691.02785
[3]	Test-rmse:3598.24092
[4]	Test-rmse:3507.51272
[5]	Test-rmse:3420.00990
[6]	Test-rmse:3334.91023
[7]	Test-rmse:3251.67982
[8]	Test-rmse:3171.67298
[9]	Test-rmse:3093.16919
[10]	Test-rmse:3017.52073
[11]	Test-rmse:2943.53189
[12]	Test-rmse:2872.47865
[13]	Test-rmse:2802.63273
[14]	Test-rmse:2735.26536
[15]	Test-rmse:2669.88117
[16]	Test-rmse:2606.17834
[17]	Test-rmse:2544.69777
[18]	Test-rmse:2485.34462
[19]	Test-rmse:2427.09087
[20]	Test-rmse:2371.01990
[21]	Test-rmse:2316.79208
[22]	Test-rmse:2264.66398
[23]	Test-rmse:2212.93694
[24]	Test-rmse:2163.31318
[25]	Test-rmse:2114.44721
[26]	Test-rmse:2067.62878
[27]	Test-rmse:2022.29661
[28]	Test-rmse:1978.63541
[29]	Test-rmse:1936.11285
[30]	Test-rmse:1895.22565
[31]	Test-rmse:1854.44373
[32]	Test-rmse:1815.64065
[33]	Test-rmse:1777.31933
[34]	Test-rmse:1740.76846
[35]	Test-rmse:1705.71709
[36]	Test-rmse:1670.28249
[37]	Test-rmse:1636.77253
[38]	Test-rmse:1604.82

[0]	Test-rmse:3936.42771
[1]	Test-rmse:3886.38100
[2]	Test-rmse:3836.92534
[3]	Test-rmse:3788.46875
[4]	Test-rmse:3740.16704
[5]	Test-rmse:3692.99107
[6]	Test-rmse:3646.10963
[7]	Test-rmse:3600.01117
[8]	Test-rmse:3554.70574
[9]	Test-rmse:3509.88489
[10]	Test-rmse:3465.95245
[11]	Test-rmse:3422.31452
[12]	Test-rmse:3379.48927
[13]	Test-rmse:3337.08107
[14]	Test-rmse:3295.32902
[15]	Test-rmse:3254.22565
[16]	Test-rmse:3213.66040
[17]	Test-rmse:3173.77084
[18]	Test-rmse:3134.50362
[19]	Test-rmse:3095.43321
[20]	Test-rmse:3057.24215
[21]	Test-rmse:3019.35181
[22]	Test-rmse:2982.20169
[23]	Test-rmse:2945.32680
[24]	Test-rmse:2909.15537
[25]	Test-rmse:2873.64720
[26]	Test-rmse:2838.70410
[27]	Test-rmse:2803.73933
[28]	Test-rmse:2769.70595
[29]	Test-rmse:2736.12977
[30]	Test-rmse:2702.89390
[31]	Test-rmse:2670.06453
[32]	Test-rmse:2637.86045
[33]	Test-rmse:2606.05213
[34]	Test-rmse:2574.86363
[35]	Test-rmse:2543.72817
[36]	Test-rmse:2513.32450
[37]	Test-rmse:2483.24044
[38]	Test-rmse:2453.43

[0]	Test-rmse:3943.06669
[1]	Test-rmse:3899.32473
[2]	Test-rmse:3856.26148
[3]	Test-rmse:3813.72490
[4]	Test-rmse:3771.45494
[5]	Test-rmse:3729.95459
[6]	Test-rmse:3688.91636
[7]	Test-rmse:3648.25071
[8]	Test-rmse:3608.04334
[9]	Test-rmse:3568.23736
[10]	Test-rmse:3528.91147
[11]	Test-rmse:3490.02939
[12]	Test-rmse:3451.57189
[13]	Test-rmse:3413.64548
[14]	Test-rmse:3376.42216
[15]	Test-rmse:3339.40195
[16]	Test-rmse:3302.73153
[17]	Test-rmse:3266.64562
[18]	Test-rmse:3230.99804
[19]	Test-rmse:3195.67131
[20]	Test-rmse:3160.85684
[21]	Test-rmse:3126.47107
[22]	Test-rmse:3092.38488
[23]	Test-rmse:3058.78645
[24]	Test-rmse:3025.62775
[25]	Test-rmse:2992.71009
[26]	Test-rmse:2960.36936
[27]	Test-rmse:2928.22126
[28]	Test-rmse:2896.65662
[29]	Test-rmse:2865.38110
[30]	Test-rmse:2834.52243
[31]	Test-rmse:2804.10017
[32]	Test-rmse:2774.00378
[33]	Test-rmse:2744.20168
[34]	Test-rmse:2714.76970
[35]	Test-rmse:2685.62139
[36]	Test-rmse:2656.85192
[37]	Test-rmse:2628.41208
[38]	Test-rmse:2600.33

3️⃣ You can find your interactive dashboard by clicking any of the  👆 wandb links above.

# Run with Sweeps

In [29]:
sweep_config = {
    'method': 'random',  # Can be grid, random, or bayesian
    'metric': {
        'name': 'RMSE',
        'goal': 'minimize'
    },
    'parameters': {
        'learning_rate': {
            'min': 0.01,
            'max': 0.03
        },
        'max_depth': {
            'values': [3, 4, 5, 6, 7, 8, 9, 10]
        },
        'subsample': {
            'min': 0.5,
            'max': 1.0
        },
        'n_estimators': {
            'values': [100]
        },
        'reg_alpha': {
            'distribution': 'log_uniform_values',
            'min': 0.001,
            'max': 10
        },
        'reg_lambda': {
            'distribution': 'log_uniform_values',
            'min': 0.01,
            'max': 100
        }
    }
}


In [30]:
sweep_id = wandb.sweep(sweep_config, project='xgboost_run')

Create sweep with ID: 0p08s3jt
Sweep URL: https://wandb.ai/msai490/xgboost_run/sweeps/0p08s3jt


In [31]:
def train():
    # Initialize a W&B run
    with wandb.init() as run:
        config = run.config

        # Assuming X_train, y_train, X_test, y_test are globally available or loaded within this function
        dtrain = xgb.DMatrix(X_train, label=y_train, enable_categorical=True)
        dtest = xgb.DMatrix(X_test, label=y_test, enable_categorical=True)

        params = {
            "objective": "reg:squarederror",
            "learning_rate": config.learning_rate,
            "max_depth": config.max_depth,
            "subsample": config.subsample,
            "n_estimators": config.n_estimators,
            "tree_method": "hist",
            "reg_alpha": config.reg_alpha,
            "reg_lambda": config.reg_lambda
        }

        # Train the model
        bst = xgb.train(params, dtrain, num_boost_round=config.n_estimators, evals=[(dtest, "Test")])

        # Evaluate the model
        predictions = bst.predict(dtest)
        rmse = mean_squared_error(y_test, predictions, squared=False)
        mae = mean_absolute_error(y_test, predictions)
        r2 = r2_score(y_test, predictions)

        # Log metrics to W&B
        wandb.log({
          "RMSE": rmse,
          "MAE": mae,
          "R2": r2
        })


In [ ]:
# Start the sweep agent
wandb.agent(sweep_id, train)

wandb: Agent Starting Run: n70ibwod with config:
wandb: 	learning_rate: 0.024381105988983187
wandb: 	max_depth: 4
wandb: 	n_estimators: 100
wandb: 	reg_alpha: 0.7067997545222084
wandb: 	reg_lambda: 26.423929228719377
wandb: 	subsample: 0.5518061878521427


[0]	Test-rmse:3900.56884
[1]	Test-rmse:3815.86293
[2]	Test-rmse:3733.33804
[3]	Test-rmse:3653.26103
[4]	Test-rmse:3574.87121
[5]	Test-rmse:3498.67446
[6]	Test-rmse:3423.91040
[7]	Test-rmse:3350.51098
[8]	Test-rmse:3280.05260
[9]	Test-rmse:3211.00023
[10]	Test-rmse:3143.91113
[11]	Test-rmse:3077.97849
[12]	Test-rmse:3014.11035
[13]	Test-rmse:2951.53566
[14]	Test-rmse:2891.08280
[15]	Test-rmse:2831.77857
[16]	Test-rmse:2773.41297
[17]	Test-rmse:2716.57696
[18]	Test-rmse:2662.41813
[19]	Test-rmse:2609.06574
[20]	Test-rmse:2556.78348
[21]	Test-rmse:2506.05491
[22]	Test-rmse:2456.44845
[23]	Test-rmse:2408.45374
[24]	Test-rmse:2361.77070
[25]	Test-rmse:2315.26030
[26]	Test-rmse:2270.26296
[27]	Test-rmse:2226.71283
[28]	Test-rmse:2184.23639
[29]	Test-rmse:2143.04397
[30]	Test-rmse:2102.45217
[31]	Test-rmse:2062.82319
[32]	Test-rmse:2024.66796
[33]	Test-rmse:1987.49878
[34]	Test-rmse:1951.75217
[35]	Test-rmse:1916.07690
[36]	Test-rmse:1882.09397
[37]	Test-rmse:1848.95527
[38]	Test-rmse:1816.14

wandb: Sweep Agent: Waiting for job.
wandb: Job received.
wandb: Agent Starting Run: pkrjof7u with config:
wandb: 	learning_rate: 0.029667410103649976
wandb: 	max_depth: 4
wandb: 	n_estimators: 100
wandb: 	reg_alpha: 0.169990987383
wandb: 	reg_lambda: 0.05623859055539372
wandb: 	subsample: 0.5319113550710679


[0]	Test-rmse:3878.86869
[1]	Test-rmse:3773.72269
[2]	Test-rmse:3671.57256
[3]	Test-rmse:3573.35496
[4]	Test-rmse:3477.20724
[5]	Test-rmse:3385.72115
[6]	Test-rmse:3295.82563
[7]	Test-rmse:3207.97241
[8]	Test-rmse:3122.58632
[9]	Test-rmse:3041.27602
[10]	Test-rmse:2962.49555
[11]	Test-rmse:2885.71207
[12]	Test-rmse:2811.92087
[13]	Test-rmse:2739.94332
[14]	Test-rmse:2670.33940
[15]	Test-rmse:2602.58193
[16]	Test-rmse:2536.61085
[17]	Test-rmse:2472.58601
[18]	Test-rmse:2412.67440
[19]	Test-rmse:2353.35200
[20]	Test-rmse:2294.95600
[21]	Test-rmse:2239.56631
[22]	Test-rmse:2185.51437
[23]	Test-rmse:2133.66699
[24]	Test-rmse:2083.31694
[25]	Test-rmse:2034.11396
[26]	Test-rmse:1986.21577
[27]	Test-rmse:1939.82669
[28]	Test-rmse:1895.34586
[29]	Test-rmse:1853.04141
[30]	Test-rmse:1812.14547
[31]	Test-rmse:1771.67081
[32]	Test-rmse:1733.79803
[33]	Test-rmse:1696.18614
[34]	Test-rmse:1660.21906
[35]	Test-rmse:1625.56671
[36]	Test-rmse:1592.73012
[37]	Test-rmse:1560.36715
[38]	Test-rmse:1528.39

wandb: Agent Starting Run: t67wyktv with config:
wandb: 	learning_rate: 0.013297820862805685
wandb: 	max_depth: 8
wandb: 	n_estimators: 100
wandb: 	reg_alpha: 0.031053013947849324
wandb: 	reg_lambda: 8.021155833279215
wandb: 	subsample: 0.5354249886586447


...

wandb: Agent Starting Run: xl2b0891 with config:
wandb: 	learning_rate: 0.020163740732755925
wandb: 	max_depth: 8
wandb: 	n_estimators: 100
wandb: 	reg_alpha: 5.867970961061681
wandb: 	reg_lambda: 0.45523645622642694
wandb: 	subsample: 0.7098536412062398


[0]	Test-rmse:3909.03288
[1]	Test-rmse:3832.48837
[2]	Test-rmse:3757.72487
[3]	Test-rmse:3684.72002
[4]	Test-rmse:3612.71096
[5]	Test-rmse:3542.68451
[6]	Test-rmse:3474.10353
[7]	Test-rmse:3406.75202
[8]	Test-rmse:3340.90416
[9]	Test-rmse:3276.22384
[10]	Test-rmse:3212.79968
[11]	Test-rmse:3150.98710
[12]	Test-rmse:3090.16439
[13]	Test-rmse:3030.66679
[14]	Test-rmse:2972.61560
[15]	Test-rmse:2915.69477
[16]	Test-rmse:2859.62258
[17]	Test-rmse:2804.97569
[18]	Test-rmse:2751.53840
[19]	Test-rmse:2698.90824
[20]	Test-rmse:2647.57977
[21]	Test-rmse:2597.15724
[22]	Test-rmse:2547.93794
[23]	Test-rmse:2499.94880
[24]	Test-rmse:2452.56619
[25]	Test-rmse:2406.10321
[26]	Test-rmse:2361.09524
[27]	Test-rmse:2316.91311
[28]	Test-rmse:2273.68075
[29]	Test-rmse:2231.01915
[30]	Test-rmse:2189.31906
[31]	Test-rmse:2148.79230
[32]	Test-rmse:2109.38421
[33]	Test-rmse:2070.51063
[34]	Test-rmse:2032.53215
[35]	Test-rmse:1995.31275
[36]	Test-rmse:1958.95091
[37]	Test-rmse:1923.23843
[38]	Test-rmse:1888.50

wandb: Agent Starting Run: 96fohqgw with config:
wandb: 	learning_rate: 0.02967866365141092
wandb: 	max_depth: 8
wandb: 	n_estimators: 100
wandb: 	reg_alpha: 0.02025391459465889
wandb: 	reg_lambda: 41.891842661396495
wandb: 	subsample: 0.968523057970856


[0]	Test-rmse:3878.95159
[1]	Test-rmse:3773.83475
[2]	Test-rmse:3672.34259
[3]	Test-rmse:3573.57567
[4]	Test-rmse:3477.73426
[5]	Test-rmse:3385.18004
[6]	Test-rmse:3295.14820
[7]	Test-rmse:3208.02994
[8]	Test-rmse:3123.29219
[9]	Test-rmse:3041.20743
[10]	Test-rmse:2961.65637
[11]	Test-rmse:2884.17551
[12]	Test-rmse:2809.09650
[13]	Test-rmse:2736.43221
[14]	Test-rmse:2666.13374
[15]	Test-rmse:2598.32421
[16]	Test-rmse:2531.78421
[17]	Test-rmse:2467.66066
[18]	Test-rmse:2405.51754
[19]	Test-rmse:2345.42367
[20]	Test-rmse:2287.34866
[21]	Test-rmse:2230.59684
[22]	Test-rmse:2175.60264
[23]	Test-rmse:2122.26629
[24]	Test-rmse:2070.30969
[25]	Test-rmse:2020.21625
[26]	Test-rmse:1971.33800
[27]	Test-rmse:1924.00949
[28]	Test-rmse:1878.57632
[29]	Test-rmse:1834.39922
[30]	Test-rmse:1791.54064
[31]	Test-rmse:1750.43379
[32]	Test-rmse:1710.44621
[33]	Test-rmse:1671.49188
[34]	Test-rmse:1633.86229
[35]	Test-rmse:1597.28233
[36]	Test-rmse:1562.18701
[37]	Test-rmse:1528.12651
[38]	Test-rmse:1494.88

wandb: Agent Starting Run: 2jbmd6o3 with config:
wandb: 	learning_rate: 0.016393988913291455
wandb: 	max_depth: 10
wandb: 	n_estimators: 100
wandb: 	reg_alpha: 0.0030555809055132373
wandb: 	reg_lambda: 0.24215383708028093
wandb: 	subsample: 0.7895182120434223


Running the XGBoost model with weights and biases sweeps seems like an efficient way to track your hyperparameters while tuning. It will keep logs of all my runs, so I do not have to retrain the model at a certain hyperparam tuning to find out how it performed. It is also a great way to compare performances across different tunings with the parallel coordinates plot in the W&B dashboard. It was also fairly easy to implement with not much extra code needed to integrate W&B.

